The expectation of the number of trials to winnow $n$ coins down to 1
=============

Supposedly a Microsoft interview question.

You're given $n$ fair coins.  You flip all of them and remove those that came up tails.
You repeat this until, after $m$ rounds of flipping,
one coin or less remains.  What's the expectation $E(m)$ of the number of rounds?

First, let's do a simulation:

In [23]:
import random

def trials(n):
    for i in range(128):
        if n <= 1: return i
        n = sum(random.randrange(2) for j in range(n))
        
trials(1024)

Unsurprisingly the number of trials $m$ required starting from $n = 2^{10} = 1024$ coins is close to $\log_2 1024 = 10$.
But $\log_2 n$ can't be the answer, because if $n = 2$, $\log_2 n = 1$, but we have a probability of $\frac 34$
of eliminating one or both coins in the first round, but a probability of $\frac 14$ of taking two or more rounds,
so the answer must be something more than 1.
So $E(m) > \log_2 n$ in that case,
rather robustly in fact, as we can confirm from experiment:

In [24]:
sum(trials(2) for i in range(1000000))/1000000

I think we can solve this case by observing that $r = E(m)_{n=2} = \frac 14\left(3 + 1(1+r)\right)$,
because in the case where it doesn't end in the first round, we're back in the same situation of two coins again,
so the expected number of rounds from that point is the same as it originally was, but we're already through
one round.

This reduces to $\frac 34r = \frac 14(3 + 1)$, so $r = \frac 43$,
which seems like a good match with the experimental result above.

How about $s = E(m)_{n=3}$?  Either 0, 1, 2, or 3 coins can come up heads, with probabilities $\frac 18, \frac 38, \frac 38, \frac 18$ respectively.  In the first two cases, we're done after one round.  In the third case,
we're back in the previous situation with 2 coins, so our expected number of rounds from that point is $r$, so
the expected total number of rounds is $1 + r$.  And in the fourth case, we're back where we started, so we need
(in expectation) $s$ more rounds, a total of $1 + s$.

So we have

$$s = \frac 18(1 + 3 + 3(1+r) + 1(1+s))$$

$$\frac 78s = \frac 18(1 + 3 + 3(1 + r) + 1)$$

$$3(1 + r) = 3\left(1 + \frac 43\right) = 3\cdot\frac 73 = 7$$

$$\begin{eqnarray}
\frac 78s &=& \frac 18(1 + 3 + 7 + 1) = \frac 18(12) = \frac{12}8 \\
s &=& \frac{12}8\cdot\frac 87 \\
  &=& \frac{12}7
\end{eqnarray}$$

In [25]:
12/7

So the expectation when $n=3$ should be about 1.714 rounds?

In [26]:
sum(trials(3) for i in range(10000))/10000

That's promising, but is it just a fluke caused by not enough trials?  I've fucked this calculation up
half a dozen ways already.

In [27]:
sum(trials(3) for i in range(10000))/10000

Seems like a pretty good result?  Let's try a larger number of trials.

In [28]:
sum(trials(3) for i in range(1000000))/1000000

In [29]:
sum(trials(3) for i in range(1000000))/1000000

We can probably extend this to more trials in the same way.  Suppose $n = 4$.  Now we can get 0, 1, 2, 3, or 4
heads, with probabilities from the binomial theorem
$\frac 1{16}, \frac 4{16}, \frac 6{16}, \frac 4{16}, \frac 1{16}$ respectively.
If we call our expected number of trials $t$ then we know

$$t = \frac 1{16}(1 + 4 + 6(1 + r) + 4(1 + s) + 1(1 + t)),$$

so

$$\begin{eqnarray}
15t &=& 1 + 4 + 6(1 + r) + 4(1 + s) + 1 \\
    &=& 1 + 4 + 6\cdot\frac 73 + 4\cdot\frac{19}7 + 1
\end{eqnarray}$$

This is pretty challenging to calculate in my head, and calling PARI/GP from Python is inconvenient,
so let's use Sympy.

In [8]:
import sympy
sympy.init_printing()

In [9]:
t = (1 + 4 + 6 * sympy.Rational(7, 3) + 4 * sympy.Rational(19, 7) + 1)/15
t

In [10]:
t.evalf()

If I've somehow managed not to totally fuck this up again, then, the average number of trials $E(m)$
starting from $n = 4$ is about 2.057?

In [11]:
sum(trials(4) for i in range(1000000))/1000000

It's a motherfucking Christmas miracle, boys.

So we can compute the answer for a given value of $n$ from the answers for all smaller $n$ by taking
the dot product of those expectations, plus 1, with the binomial probabilities for the first trial,
and then dividing by
the appropriate power of 2, minus one.

This will always be a rational number, but I don't know how to go about trying to find a closed-form formula for it.
The question didn't ask for a closed-form formula, though, but for a callable subroutine, and the above
can be straightforwardly converted into such a subroutine.  I don't think I'll do that tonight, but
because Python arithmetic transparently overflows to bignums, you can just use the binomial-coefficient
formula directly if you want:

In [21]:
def nCm(n, m):
    return factorial(n)//factorial(m)//factorial(n-m)

def factorial(n):
    result = 1
    for i in range(n):
        result *= i+1
    return result

[nCm(4, i) for i in range(0, 5)]

It even works reasonably fast for these purposes,
despite computing unreasonably large intermediate results:

In [20]:
factorial(100)

In [22]:
%%time
nCm(100, 1)

CPU times: user 46 µs, sys: 4 µs, total: 50 µs
Wall time: 58.2 µs
